In [32]:
#pip install nengo

In [33]:
%matplotlib inline

from keras.utils import np_utils
import nengo
import tensorflow as tf
import numpy as np
import matplotlib.pyplot as plt
import os
import datetime
from os import listdir
from keras.models import Sequential
from keras.layers import Dense, Dropout, Conv2D, MaxPool2D, Flatten, BatchNormalization, LeakyReLU
from keras.callbacks import EarlyStopping

import nengo_dl



In [34]:
#pip install nengo_dl

### Uploading all of my spectrogram images as a numpy array

In [35]:
images = list()

for filename in listdir('F:/bci/colored/all_spec'):
    img_data = plt.imread('F:/bci/colored/all_spec/' +\
                       filename)
    img_data = np.asarray(img_data)

    images.append(img_data)

    print('> loaded %s images' % (len(images)))
    
images = np.array(images)

print(images.shape)

> loaded 1 images
> loaded 2 images
> loaded 3 images
> loaded 4 images
> loaded 5 images
> loaded 6 images
> loaded 7 images
> loaded 8 images
> loaded 9 images
> loaded 10 images
> loaded 11 images
> loaded 12 images
> loaded 13 images
> loaded 14 images
> loaded 15 images
> loaded 16 images
> loaded 17 images
> loaded 18 images
> loaded 19 images
> loaded 20 images
> loaded 21 images
> loaded 22 images
> loaded 23 images
> loaded 24 images
> loaded 25 images
> loaded 26 images
> loaded 27 images
> loaded 28 images
> loaded 29 images
> loaded 30 images
> loaded 31 images
> loaded 32 images
> loaded 33 images
> loaded 34 images
> loaded 35 images
> loaded 36 images
> loaded 37 images
> loaded 38 images
> loaded 39 images
> loaded 40 images
> loaded 41 images
> loaded 42 images
> loaded 43 images
> loaded 44 images
> loaded 45 images
> loaded 46 images
> loaded 47 images
> loaded 48 images
> loaded 49 images
> loaded 50 images
> loaded 51 images
> loaded 52 images
> loaded 53 images
> 

> loaded 424 images
> loaded 425 images
> loaded 426 images
> loaded 427 images
> loaded 428 images
> loaded 429 images
> loaded 430 images
> loaded 431 images
> loaded 432 images
> loaded 433 images
> loaded 434 images
> loaded 435 images
> loaded 436 images
> loaded 437 images
> loaded 438 images
> loaded 439 images
> loaded 440 images
> loaded 441 images
> loaded 442 images
> loaded 443 images
> loaded 444 images
> loaded 445 images
> loaded 446 images
> loaded 447 images
> loaded 448 images
> loaded 449 images
> loaded 450 images
> loaded 451 images
> loaded 452 images
> loaded 453 images
> loaded 454 images
> loaded 455 images
> loaded 456 images
> loaded 457 images
> loaded 458 images
> loaded 459 images
> loaded 460 images
> loaded 461 images
> loaded 462 images
> loaded 463 images
> loaded 464 images
> loaded 465 images
> loaded 466 images
> loaded 467 images
> loaded 468 images
> loaded 469 images
> loaded 470 images
> loaded 471 images
> loaded 472 images
> loaded 473 images


> loaded 849 images
> loaded 850 images
> loaded 851 images
> loaded 852 images
> loaded 853 images
> loaded 854 images
> loaded 855 images
> loaded 856 images
> loaded 857 images
> loaded 858 images
> loaded 859 images
> loaded 860 images
> loaded 861 images
> loaded 862 images
> loaded 863 images
> loaded 864 images
> loaded 865 images
> loaded 866 images
> loaded 867 images
> loaded 868 images
> loaded 869 images
> loaded 870 images
> loaded 871 images
> loaded 872 images
> loaded 873 images
> loaded 874 images
> loaded 875 images
> loaded 876 images
> loaded 877 images
> loaded 878 images
> loaded 879 images
> loaded 880 images
> loaded 881 images
> loaded 882 images
> loaded 883 images
> loaded 884 images
> loaded 885 images
> loaded 886 images
> loaded 887 images
> loaded 888 images
> loaded 889 images
> loaded 890 images
> loaded 891 images
> loaded 892 images
> loaded 893 images
> loaded 894 images
> loaded 895 images
> loaded 896 images
> loaded 897 images
> loaded 898 images


> loaded 1279 images
> loaded 1280 images
> loaded 1281 images
> loaded 1282 images
> loaded 1283 images
> loaded 1284 images
> loaded 1285 images
> loaded 1286 images
> loaded 1287 images
> loaded 1288 images
> loaded 1289 images
> loaded 1290 images
> loaded 1291 images
> loaded 1292 images
> loaded 1293 images
> loaded 1294 images
> loaded 1295 images
> loaded 1296 images
> loaded 1297 images
> loaded 1298 images
> loaded 1299 images
> loaded 1300 images
> loaded 1301 images
> loaded 1302 images
> loaded 1303 images
> loaded 1304 images
> loaded 1305 images
> loaded 1306 images
> loaded 1307 images
> loaded 1308 images
> loaded 1309 images
> loaded 1310 images
> loaded 1311 images
> loaded 1312 images
> loaded 1313 images
> loaded 1314 images
> loaded 1315 images
> loaded 1316 images
> loaded 1317 images
> loaded 1318 images
> loaded 1319 images
> loaded 1320 images
> loaded 1321 images
> loaded 1322 images
> loaded 1323 images
> loaded 1324 images
> loaded 1325 images
> loaded 1326

### Labelling

In the folder the first 808 images are actually '1' and the rest label to '0'. To make the labels, i have concatenated np.ones() + np.zeroes() arrays to match. 

In [36]:
test_labels1 = np.ones((808,))
test_labels0 = np.zeros((808,))
labels = np.concatenate((test_labels1, test_labels0))
labels.shape

(1616,)

In [37]:
from sklearn.model_selection import train_test_split
train_images, test_images, train_labels, test_labels = train_test_split(images, labels, test_size = 0.25, random_state = 97)
print(train_images.shape,test_images.shape,train_labels.shape,test_labels.shape)

(1212, 112, 112, 3) (404, 112, 112, 3) (1212,) (404,)


In [10]:
#reshaping 
train_images = train_images.reshape((train_images.shape[0], 1, -1))
train_labels = train_labels.reshape((train_labels.shape[0], 1, -1))
test_images = test_images.reshape((test_images.shape[0], 1, -1))
test_labels = test_labels.reshape((test_labels.shape[0], 1, -1))
print(train_images.shape,test_images.shape,train_labels.shape,test_labels.shape)

(1212, 1, 37632) (404, 1, 37632) (1212, 1, 1) (404, 1, 1)


In [14]:
train_images = train_images.astype('float32')
test_images = test_images.astype('float32')

# train_images /=255
# test_images /=255
train_images[0,0,].shape

(37632,)

In [15]:
test_images

array([[[130., 110., 225., ..., 244., 253.,  84.]],

       [[130., 110., 225., ..., 255., 247.,  87.]],

       [[129., 110., 225., ..., 246., 253.,  85.]],

       ...,

       [[130., 111., 226., ..., 246., 252.,  90.]],

       [[130., 110., 223., ..., 246., 254.,  80.]],

       [[129., 111., 221., ..., 238., 244.,  84.]]], dtype=float32)

In [16]:
for i in range(train_images.shape[0]): # normalizing data
    for j in range(train_images.shape[2]):
        train_images[i,0,j] -=np.mean(train_images[i])
        train_images[i,0,j] /=np.std(train_images[i])
        
for k in range(test_images.shape[0]):
    for l in range(test_images.shape[2]):
        test_images[k,0,l] -=np.mean(test_images[k])
        test_images[k,0,l] /=np.std(test_images[k])        

    

In [17]:
test_images 

array([[[ 2.3961353e-01, -3.2551870e-02,  1.5327023e+00, ...,
          7.8366470e+01,  8.7978119e+01,  3.2014698e+01]],

       [[ 2.7819759e-01, -1.4306280e-03,  1.6067382e+00, ...,
          8.1813911e+01,  8.6446747e+01,  3.3256050e+01]],

       [[ 2.2404373e-01, -3.4313727e-02,  1.5297453e+00, ...,
          7.8889534e+01,  8.7945709e+01,  3.2386326e+01]],

       ...,

       [[ 2.3825139e-01, -1.9922901e-02,  1.5430268e+00, ...,
          7.8843552e+01,  8.7537537e+01,  3.4256489e+01]],

       [[ 2.4214841e-01, -2.9685250e-02,  1.5064712e+00, ...,
          7.8910995e+01,  8.8322540e+01,  3.0498156e+01]],

       [[ 2.2564386e-01, -1.9214606e-02,  1.4774562e+00, ...,
          7.7130196e+01,  8.5367310e+01,  3.2004395e+01]]], dtype=float32)

In [18]:
inp = tf.keras.Input(shape=(112, 112, 3)) # building a simple cnn model (from nengo documentation)

# convolutional layers
conv0 = tf.keras.layers.Conv2D(
    filters=32,
    kernel_size=3,
    activation=tf.nn.relu,
)(inp)

conv1 = tf.keras.layers.Conv2D(
    filters=64,
    kernel_size=3,
    strides=2,
    activation=tf.nn.relu,
)(conv0)

# fully connected layer
dropout = tf.keras.layers.Dropout(0.5)(conv1)
flatten = tf.keras.layers.Flatten()(dropout)

dense = tf.keras.layers.Dense(units=10)(flatten)
op = tf.keras.layers.Dense(units=1, activation = tf.nn.sigmoid)(dense)
model = tf.keras.Model(inputs=inp, outputs=op)

In [20]:
converter = nengo_dl.Converter(model)

C:\Users\HP\anaconda3\lib\site-packages\nengo_dl\converter.py:324: UserWarning: Layer type Dropout does not have a registered converter. Falling back to TensorNode.
  warnings.warn(


In [21]:
log_dir = "logs/fit/" + datetime.datetime.now().strftime("%Y%m%d-%H%M%S")
tensorboard_callback = tf.keras.callbacks.TensorBoard(log_dir=log_dir, histogram_freq=1)

In [22]:
with nengo_dl.Simulator(converter.net, minibatch_size=100) as sim:
        # run training
        sim.compile(
            optimizer=tf.optimizers.RMSprop(lr=0.001),
            loss=tf.losses.BinaryCrossentropy(from_logits=True),
            metrics=tf.keras.metrics.BinaryAccuracy()
        )
        sim.fit(
            {converter.inputs[inp]: train_images},
            {converter.outputs[op]: train_labels},
            validation_data=(
                {converter.inputs[inp]: test_images},
                {converter.outputs[op]: test_labels},
            ),
            epochs=5,
            callbacks=[tensorboard_callback]
        )

        # save the parameters to file
        sim.save_params("./keras_to_snn_params_spec")

|                     Building network (0%)                    | ETA:  --:--:--

C:\Users\HP\anaconda3\lib\site-packages\nengo_dl\simulator.py:460: UserWarning: No GPU support detected. See https://www.nengo.ai/nengo-dl/installation.html#installing-tensorflow for instructions on setting up TensorFlow with GPU support.
  warnings.warn(


Build finished in 0:00:05                                                      
Optimization finished in 0:00:00                                               
Construction finished in 0:00:00                                               


C:\Users\HP\anaconda3\lib\site-packages\keras\optimizer_v2\rmsprop.py:130: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  super(RMSprop, self).__init__(name, **kwargs)
C:\Users\HP\anaconda3\lib\site-packages\nengo_dl\simulator.py:1921: UserWarning: Number of elements in input data (404) is not evenly divisible by Simulator.minibatch_size (100); input data will be truncated.
  warnings.warn(
C:\Users\HP\anaconda3\lib\site-packages\nengo_dl\simulator.py:1921: UserWarning: Number of elements in input data (1212) is not evenly divisible by Simulator.minibatch_size (100); input data will be truncated.
  warnings.warn(


Epoch 1/5
12/12 [==============================] - 232s 14s/step - loss: 0.7003 - probe_loss: 0.7003 - probe_binary_accuracy: 0.4842 - val_loss: 0.6931 - val_probe_loss: 0.6931 - val_probe_binary_accuracy: 0.5150
Epoch 2/5
12/12 [==============================] - 130s 11s/step - loss: 0.6931 - probe_loss: 0.6931 - probe_binary_accuracy: 0.4942 - val_loss: 0.6931 - val_probe_loss: 0.6931 - val_probe_binary_accuracy: 0.5150
Epoch 3/5
12/12 [==============================] - 127s 11s/step - loss: 0.6931 - probe_loss: 0.6931 - probe_binary_accuracy: 0.4942 - val_loss: 0.6931 - val_probe_loss: 0.6931 - val_probe_binary_accuracy: 0.5150
Epoch 4/5
12/12 [==============================] - 130s 11s/step - loss: 0.6931 - probe_loss: 0.6931 - probe_binary_accuracy: 0.4942 - val_loss: 0.6931 - val_probe_loss: 0.6931 - val_probe_binary_accuracy: 0.5150
Epoch 5/5
12/12 [==============================] - 129s 11s/step - loss: 0.6931 - probe_loss: 0.6931 - probe_binary_accuracy: 0.4942 - val_loss: 0.6

In [23]:
%load_ext tensorboard

In [24]:
%tensorboard --logdir logs/fit

Reusing TensorBoard on port 6006 (pid 13680), started 1 day, 4:15:23 ago. (Use '!kill 13680' to kill it.)

In [27]:
# predicting using the model (from nengo documentation)
    
activation=nengo.SpikingRectifiedLinear()
params_file="keras_to_snn_params_spec"
n_steps=30
scale_firing_rates=1
synapse=None
n_test=404
    
    

nengo_converter = nengo_dl.Converter(
    model,
    swap_activations={tf.nn.relu: activation},
    scale_firing_rates=scale_firing_rates,
    synapse=synapse,
)

nengo_input = nengo_converter.inputs[inp]
nengo_output = nengo_converter.outputs[op]

sample_neurons = np.linspace(
    0,
    np.prod(conv0.shape[1:]),
    1000,
    endpoint=False,
    dtype=np.int32,
)
with nengo_converter.net:
    conv0_probe = nengo.Probe(nengo_converter.layers[conv0][sample_neurons])


tiled_test_images = np.tile(test_images[:n_test], (1, n_steps, 1))


with nengo_converter.net:
    nengo_dl.configure_settings(stateful=False)


with nengo_dl.Simulator(
    nengo_converter.net, minibatch_size=10, progress_bar=False
) as nengo_sim:
    nengo_sim.load_params(params_file)
    data = nengo_sim.predict({nengo_input: tiled_test_images})

# compute accuracy on test data, using output of network on
# last timestep
predictions = np.argmax(data[nengo_output][:, -1], axis=-1)


# please ignore the below error, 

    

C:\Users\HP\AppData\Local\Temp/ipykernel_14908/542056853.py:50: DeprecationWarning: elementwise comparison failed; this will raise an error in the future.
  accuracy = (predictions == test_labels[:n_test, 0, 0]).mean()


AttributeError: 'bool' object has no attribute 'mean'

In [28]:
predictions  #predictions are all zeroes 

array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,

In [39]:
test_labels

array([0., 1., 0., 0., 0., 0., 1., 0., 0., 1., 1., 0., 0., 0., 0., 0., 1.,
       1., 0., 0., 1., 0., 1., 0., 0., 1., 0., 0., 0., 0., 1., 1., 0., 0.,
       0., 1., 0., 0., 0., 1., 1., 0., 0., 1., 0., 1., 0., 1., 0., 1., 0.,
       1., 1., 1., 0., 0., 0., 1., 1., 1., 0., 1., 0., 1., 0., 0., 0., 1.,
       1., 0., 1., 1., 0., 0., 0., 1., 0., 0., 1., 0., 1., 0., 1., 1., 1.,
       0., 1., 0., 1., 1., 0., 0., 1., 1., 1., 1., 0., 1., 0., 1., 0., 0.,
       0., 0., 0., 1., 0., 0., 1., 0., 0., 0., 0., 0., 1., 1., 1., 1., 1.,
       1., 1., 1., 1., 0., 0., 0., 0., 0., 1., 0., 0., 1., 1., 1., 0., 0.,
       0., 0., 0., 0., 0., 1., 1., 1., 1., 0., 0., 0., 0., 0., 1., 0., 0.,
       0., 1., 1., 0., 1., 1., 0., 1., 1., 0., 0., 1., 1., 1., 1., 0., 0.,
       1., 0., 1., 0., 1., 1., 1., 0., 1., 1., 0., 1., 0., 1., 0., 0., 1.,
       0., 1., 1., 1., 1., 1., 1., 1., 1., 1., 0., 0., 1., 1., 1., 1., 0.,
       0., 1., 0., 0., 0., 1., 0., 1., 1., 1., 0., 1., 0., 0., 0., 1., 1.,
       0., 0., 0., 1., 1.

In [41]:
data[nengo_output][:,-1]

array([[0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],